This code is used to calculate mAP

In [1]:
import numpy as np
import xml.etree.ElementTree as ET
import os
import pickle
detpath = 'eval/2/{}.txt'
annopath = './data/VOCdevkit/VOC2007/Annotations/{}.xml'
imagesetfile = './imagenames.txt'
output_path = 'output'
cachedir = 'master'
classes = np.array([
        'aeroplane',
        'bicycle',
        'bird',
        'boat',
        'bottle',
        'bus',
        'car',
        'cat',
        'chair',
        'cow',
        'diningtable',
        'dog',
        'horse',
        'motorbike',
        'person',
        'pottedplant',
        'sheep',
        'sofa',
        'train',
        'tvmonitor',
    ])

In [2]:
def parse_rec(filename):
    tree = ET.parse(filename)
    objects = []
    for obj in tree.findall('object'):
        obj_struct = {}
        obj_struct['name'] = obj.find('name').text
        obj_struct['pose'] = obj.find('pose').text
        obj_struct['truncated'] = int(obj.find('truncated').text)
        obj_struct['difficult'] = int(obj.find('difficult').text)
        bbox = obj.find('bndbox')
        obj_struct['bbox'] = [int(bbox.find('xmin').text),
                              int(bbox.find('ymin').text),
                              int(bbox.find('xmax').text),
                              int(bbox.find('ymax').text)]
        objects.append(obj_struct)
        
    return objects

In [3]:
def voc_eval(detpath,
             annopath,
             imagesetfile,
             classname,
             cachedir,
             ovthres=0.5,
             use_diff=False):
    if not os.path.isdir(cachedir):
        os.mkdir(cachedir)
    cachefile = os.path.join(cachedir, 'annots.pkl')
    
    with open(imagesetfile, 'r') as f:
        lines = f.readlines()
    imagenames = [x.strip() for x in lines]
    
    if not os.path.isfile(cachefile):
        
        recs = {}
        for i, imagename in enumerate(imagenames):
            recs[imagename] = parse_rec(annopath.format(imagename))
            if i % 100 == 0:
                print('Reading annotation for {:d}/{:d}'.format(i+1, len(imagenames)))
        print('Saving cached annotations to {:s}'.format(cachefile))
        with open(cachefile, 'wb') as f:
            pickle.dump(recs, f)
    else:
        with open(cachefile, 'rb') as f:
            try:
                recs = pickle.load(f)
            except:
                recs = pickle.load(f, encoding='bytes')           

    class_recs = {}
    npos = 0
    for imagename in imagenames:
        R = [obj for obj in recs[imagename] if obj['name'] == classname]
        bbox = np.array([x['bbox'] for x in R])
        if use_diff:
            difficult = np.array([False for x in R]).astype(np.bool)
        else:
            difficult = np.array([x['difficult'] for x in R]).astype(np.bool)
        print(imagename, difficult, sum(~difficult))
        det = [False] * len(R)
        npos = npos + sum(~difficult)
        class_recs[imagename] = {'bbox': bbox,
                                 'difficult': difficult,
                                 'det': det}
    print(npos)
    detfile = detpath.format(classname)
    with open(detfile, 'r') as f:
        lines = f.readlines()
    splitlines = [x.strip().split(' ') for x in lines]
    image_ids = [x[0].replace('.jpg', '') for x in splitlines]
    confidence = np.array([float(x[1]) for x in splitlines])
    BB = np.array([[float(z) for z in x[2:]] for x in splitlines])
    
    nd = len(image_ids)
    tp = np.zeros(nd)
    fp = np.zeros(nd)
    
    if BB.shape[0] > 0:
        sorted_ind = np.argsort(-confidence)
        sorted_scores = np.sort(-confidence)
        BB = BB[sorted_ind, :]
        image_ids = [image_ids[x] for x in sorted_ind]
        
        for d in range(nd):
            
            R = class_recs[image_ids[d]]
            bb = BB[d, :].astype(float)
            ovmax = -np.inf
            BBGT = R['bbox'].astype(float)
            
            if BBGT.size > 0:
                ixmin = np.maximum(BBGT[:, 0], bb[0])
                iymin = np.maximum(BBGT[:, 1], bb[1])
                ixmax = np.minimum(BBGT[:, 2], bb[2])
                iymax = np.minimum(BBGT[:, 3], bb[3])
                iw = np.maximum(ixmax - ixmin + 1., 0.)
                ih = np.maximum(iymax - iymin + 1., 0.)
                inters = iw * ih
                
                uni = ((bb[2] - bb[0] + 1.) * (bb[3] - bb[1] + 1.) + 
                       (BBGT[:, 2] - BBGT[:, 0] + 1.) *
                       (BBGT[:, 3] - BBGT[:, 1] + 1.) - inters)
                
                overlaps = inters / uni
                ovmax = np.max(overlaps)
                jmax = np.argmax(overlaps)
            if ovmax > ovthres:
                if not R['difficult'][jmax]:
                    if not R['det'][jmax]:
                        tp[d] = 1
                        R['det'][jmax] = 1
                    else:
                        fp[d] = 1.
            else:
                print(image_ids[d], bb, BBGT)
                fp[d] = 1.
                
    fp = np.cumsum(fp)
    tp = np.cumsum(tp)
    rec = tp / float(npos)
        
    prec = tp / np.maximum(tp + fp, np.finfo(np.float64).eps)
    ap = voc_ap(rec, prec)
        
    return rec, prec, ap

In [4]:
def voc_ap(rec, prec):
    ap = 0.
    for t in np.arange(0., 1.1, 0.1):
        if np.sum(rec >= t) == 0:
            p = 0
        else:
            p = np.max(prec[rec >= t])
        ap = ap + p / 11
    return ap

In [5]:
if __name__ == '__main__':
    output = []
    ap_all = []
    for name in classes:
        
        rec, prec, ap = voc_eval(detpath, annopath, imagesetfile, name, cachedir)
        ap_all.append(ap)
        output.append('%-11s'%(name) + ' ' + '%.4f' %(ap) + '\n')
    ap_all = np.array(ap_all)
    mAP = np.mean(ap_all)
    output.append('%-11s'%('mAP') + ' ' + '%.4f'%(mAP) + '\n')
    with open(os.path.join(output_path, '2.txt'), 'w') as f:
        f.writelines(output)

000001 [] 0
000002 [] 0
000003 [] 0
000004 [] 0
000006 [] 0
000008 [] 0
000010 [] 0
000011 [] 0
000013 [] 0
000014 [] 0
000015 [] 0
000018 [] 0
000022 [] 0
000025 [] 0
000027 [] 0
000028 [] 0
000029 [] 0
000031 [] 0
000037 [] 0
000038 [] 0
000040 [] 0
000043 [] 0
000045 [] 0
000049 [] 0
000053 [] 0
000054 [] 0
000055 [] 0
000056 [] 0
000057 [] 0
000058 [] 0
000059 [] 0
000062 [] 0
000067 [False] 1
000068 [] 0
000069 [] 0
000070 [] 0
000071 [] 0
000074 [] 0
000075 [] 0
000076 [] 0
000079 [] 0
000080 [] 0
000082 [] 0
000084 [] 0
000085 [] 0
000086 [] 0
000087 [] 0
000088 [] 0
000090 [] 0
000092 [] 0
000094 [] 0
000096 [] 0
000097 [] 0
000098 [] 0
000100 [] 0
000103 [] 0
000105 [] 0
000106 [] 0
000108 [] 0
000111 [] 0
000114 [] 0
000115 [] 0
000116 [] 0
000119 [] 0
000124 [] 0
000126 [] 0
000127 [] 0
000128 [False] 1
000135 [] 0
000136 [] 0
000137 [] 0
000139 [] 0
000144 [] 0
000145 [] 0
000148 [] 0
000149 [] 0
000151 [] 0
000152 [] 0
000155 [] 0
000157 [] 0
000160 [] 0
000166 [] 0
000167

002299 [] 0
002301 [] 0
002303 [] 0
002304 [] 0
002309 [] 0
002312 [] 0
002313 [] 0
002314 [] 0
002316 [] 0
002317 [] 0
002319 [] 0
002322 [] 0
002325 [] 0
002326 [] 0
002327 [] 0
002331 [] 0
002336 [] 0
002338 [] 0
002339 [] 0
002341 [] 0
002344 [] 0
002346 [] 0
002349 [] 0
002351 [] 0
002353 [] 0
002356 [] 0
002357 [False] 1
002358 [] 0
002360 [] 0
002363 [] 0
002365 [] 0
002370 [] 0
002379 [] 0
002380 [] 0
002381 [] 0
002383 [] 0
002386 [] 0
002388 [] 0
002389 [] 0
002390 [] 0
002394 [] 0
002395 [] 0
002396 [] 0
002397 [] 0
002398 [] 0
002399 [] 0
002400 [] 0
002402 [] 0
002406 [] 0
002408 [] 0
002409 [] 0
002412 [] 0
002414 [] 0
002416 [] 0
002418 [] 0
002421 [] 0
002422 [] 0
002424 [] 0
002426 [] 0
002428 [] 0
002429 [] 0
002430 [] 0
002431 [] 0
002432 [] 0
002434 [] 0
002438 [] 0
002440 [] 0
002446 [] 0
002447 [] 0
002449 [] 0
002451 [] 0
002453 [] 0
002455 [] 0
002457 [] 0
002463 [] 0
002464 [] 0
002467 [False False False False] 4
002469 [] 0
002473 [] 0
002474 [] 0
002475 [] 0


004664 [] 0
004665 [] 0
004666 [] 0
004667 [] 0
004668 [] 0
004669 [] 0
004670 [] 0
004677 [] 0
004678 [] 0
004680 [False] 1
004681 [] 0
004684 [] 0
004688 [] 0
004690 [] 0
004695 [] 0
004696 [] 0
004697 [] 0
004698 [] 0
004700 [] 0
004703 [] 0
004704 [] 0
004709 [] 0
004711 [] 0
004712 [] 0
004713 [] 0
004716 [] 0
004717 [] 0
004720 [] 0
004721 [] 0
004724 [] 0
004725 [] 0
004726 [] 0
004728 [] 0
004729 [] 0
004730 [] 0
004731 [] 0
004733 [] 0
004734 [] 0
004736 [] 0
004738 [] 0
004739 [] 0
004740 [] 0
004741 [] 0
004744 [] 0
004745 [] 0
004749 [] 0
004751 [] 0
004752 [False] 1
004755 [] 0
004756 [] 0
004757 [] 0
004758 [] 0
004759 [] 0
004762 [] 0
004763 [] 0
004764 [] 0
004765 [] 0
004766 [] 0
004767 [] 0
004769 [] 0
004771 [] 0
004772 [] 0
004774 [] 0
004775 [] 0
004778 [] 0
004780 [] 0
004781 [] 0
004784 [False] 1
004787 [] 0
004791 [] 0
004795 [] 0
004798 [] 0
004800 [] 0
004802 [] 0
004803 [] 0
004804 [] 0
004806 [] 0
004807 [] 0
004809 [] 0
004810 [] 0
004811 [] 0
004813 [] 0
0

007378 [] 0
007379 [] 0
007380 [] 0
007382 [] 0
007384 [] 0
007386 [] 0
007387 [] 0
007391 [] 0
007392 [] 0
007393 [] 0
007395 [] 0
007397 [] 0
007399 [] 0
007400 [] 0
007401 [] 0
007402 [] 0
007403 [False] 1
007404 [] 0
007405 [] 0
007406 [] 0
007407 [] 0
007409 [] 0
007412 [] 0
007415 [] 0
007418 [] 0
007420 [] 0
007423 [] 0
007426 [] 0
007428 [] 0
007429 [] 0
007430 [] 0
007434 [] 0
007440 [] 0
007441 [] 0
007442 [] 0
007444 [] 0
007447 [] 0
007450 [] 0
007452 [] 0
007453 [] 0
007455 [] 0
007456 [] 0
007459 [] 0
007462 [] 0
007463 [] 0
007464 [] 0
007469 [] 0
007471 [] 0
007472 [] 0
007473 [] 0
007476 [] 0
007478 [] 0
007485 [] 0
007487 [] 0
007488 [] 0
007492 [] 0
007494 [] 0
007495 [] 0
007496 [] 0
007499 [] 0
007500 [] 0
007501 [] 0
007502 [False] 1
007504 [] 0
007505 [] 0
007507 [] 0
007508 [] 0
007509 [] 0
007510 [] 0
007512 [] 0
007514 [] 0
007515 [] 0
007516 [] 0
007518 [] 0
007520 [] 0
007522 [] 0
007529 [] 0
007531 [] 0
007532 [] 0
007534 [] 0
007539 [] 0
007541 [] 0
007542

007825 [ 64.  64. 466. 332.] [[ 28. 125. 477. 254.]]
008459 [ 82.  98. 490. 374.] [[170. 238. 500. 334.]
 [107. 179. 270. 249.]
 [157. 175. 292. 213.]
 [136. 176. 225. 199.]
 [359. 154. 450. 186.]
 [439. 149. 500. 192.]]
000618 [174.  89. 450. 253.] [[  1.  35. 150. 212.]
 [124.  35. 489. 291.]]
003478 [336.   1. 493. 125.] [[422.  14. 473.  71.]]
001929 [142.  89. 408. 259.] [[205. 145. 362. 196.]]
000473 [319.  50. 495. 235.] [[415. 120. 460. 153.]]
004572 [133.  96. 371. 323.] [[235. 241. 279. 296.]]
002014 [ 43.  93. 306. 282.] [[132. 146. 195. 206.]]
006051 [141. 113. 418. 294.] [[158. 159. 220. 183.]
 [249. 188. 309. 210.]
 [320. 199. 381. 225.]
 [304. 221. 366. 242.]
 [381. 227. 442. 250.]
 [431. 258. 493. 283.]]
000665 [114. 130. 393. 339.] [[138. 176. 381. 261.]]
002052 [228.  42. 477. 259.] [[ 38.  19. 479. 250.]]
002822 [ 79.  36. 358. 242.] [[189. 103. 225. 125.]]
008825 [ 75.  63. 456. 332.] [[143. 128. 400. 211.]]
008825 [ 75.  63. 456. 332.] [[143. 128. 400. 211.]]
00898

...

009854 [] 0
009856 [] 0
009857 [] 0
009861 [] 0
009864 [] 0
009866 [] 0
009871 [] 0
009873 [] 0
009875 [] 0
009876 [] 0
009883 [] 0
009885 [] 0
009888 [False] 1
009889 [] 0
009890 [] 0
009891 [] 0
009892 [] 0
009893 [] 0
009895 [] 0
009899 [] 0
009901 [] 0
009903 [] 0
009906 [False False False False] 4
009907 [] 0
009909 [] 0
009910 [] 0
009912 [] 0
009914 [ True  True] 0
009915 [] 0
009916 [] 0
009919 [] 0
009921 [] 0
009922 [] 0
009924 [] 0
009925 [] 0
009927 [] 0
009928 [] 0
009929 [] 0
009930 [] 0
009931 [] 0
009933 [] 0
009934 [] 0
009936 [] 0
009937 [] 0
009941 [] 0
009943 [] 0
009948 [] 0
009951 [] 0
009952 [] 0
009953 [] 0
009956 [] 0
009957 [] 0
009960 [] 0
009962 [] 0
009963 [] 0
308
002985 [158.  36. 389. 233.] [[194.  15. 475. 273.]]
002356 [ 14.  60. 486. 352.] [[  4.  54. 158. 223.]]
008428 [150.  14. 481. 314.] [[170.  10. 339. 161.]]
002997 [ 43.  11. 478. 361.] [[263.   8. 500. 272.]]
006116 [ 95.  84. 372. 269.] [[169.  98. 343. 232.]]
009357 [ 65.  85. 477. 374.] [[3

008938 [  0.  55. 303. 499.] []
008957 [ 15.  64. 441. 374.] []
008957 [ 15.  64. 441. 374.] []
008938 [  0.  55. 303. 499.] []
004855 [ 17.   7. 473. 353.] []
005480 [ 21.  19. 489. 404.] []
001415 [  8.   5. 474. 315.] []
001921 [ 46. 127. 369. 499.] []
008363 [ 27.  35. 410. 333.] []
002451 [ 20.  27. 459. 351.] []
005296 [  4.  19. 482. 365.] []
000551 [  8.  11. 363. 253.] []
007366 [ 17.  12. 305. 499.] []
002119 [ 17.  23. 491. 364.] [[369. 135. 443. 202.]]
001581 [ 14.  27. 286. 373.] []
002644 [ 14.  95. 263. 345.] []
003079 [  6.  93. 495. 368.] []
000029 [ 37.  48. 323. 311.] []
003744 [  3.   7. 478. 232.] []
007783 [ 10.   0. 402. 290.] []
003067 [  8.  36. 489. 361.] []
001081 [ 23.  13. 494. 371.] [[403. 153. 461. 230.]]
007472 [ 91.  78. 494. 368.] []
007784 [  0.   0. 370. 229.] []
001600 [132.  21. 469. 369.] []
004559 [  4.   0. 485. 294.] []
001123 [ 15.   9. 491. 316.] []
006985 [  8.  21. 484. 324.] []
007782 [ 35.  43. 494. 373.] []
006057 [ 25.  95. 465. 325.] [

007406 [ 46.  27. 482. 360.] []
001449 [ 10.   5. 492. 297.] []
001099 [ 15.  12. 489. 355.] []
008598 [ 10.  26. 469. 286.] []
001232 [ 49.  99. 484. 311.] []
003931 [  4.  27. 493. 374.] []
001791 [  7.   5. 446. 476.] []
007588 [ 40.  53. 487. 332.] []
003940 [  9.  10. 487. 303.] []
005642 [  6.  11. 489. 365.] []
000529 [  0.   4. 489. 358.] []
000928 [  9.   0. 481. 355.] []
008089 [ 37.  34. 409. 317.] []
003156 [ 17.  14. 492. 318.] []
008505 [ 40.  35. 499. 360.] []
007823 [  2.  17. 438. 336.] []
002876 [ 11.  12. 484. 358.] []
004116 [ 13.  20. 485. 321.] []
009403 [ 28.   0. 290. 236.] []
006048 [ 72.  20. 310. 461.] []
000247 [ 15.  17. 368. 493.] []
003020 [ 32.  10. 482. 368.] []
000326 [ 30.  15. 494. 356.] []
000098 [ 13.  92. 349. 260.] []
005287 [ 10.   8. 486. 310.] []
008182 [ 20.   8. 411. 261.] []
007041 [ 29.  19. 364. 395.] []
007044 [ 70.  76. 372. 472.] []
002583 [ 20.  19. 494. 369.] []
006080 [  1.   4. 495. 497.] []
004900 [ 23.  10. 154. 455.] []
004620 [

002071 [  5.  18. 480. 325.] []
004026 [  7.  40. 477. 369.] []
003457 [ 13.   6. 368. 488.] []
006566 [  8.   4. 206. 242.] []
001891 [  7.   7. 487. 334.] []
000693 [  7.  17. 457. 365.] []
009415 [116.  39. 473. 320.] []
007063 [ 33.  44. 479. 357.] []
003062 [  8.  19. 492. 366.] []
003428 [  5.  10. 489. 330.] []
006094 [ 15.  17. 493. 370.] []
005797 [  4.  37. 488. 371.] []
006577 [ 31.   6. 491. 368.] []
003268 [ 15.  12. 480. 208.] []
003474 [ 10.  20. 454. 357.] []
006491 [ 10.  18. 486. 161.] []
006490 [  7.   6. 261. 328.] []
003976 [ 13.  11. 318. 482.] []
002084 [ 12.  19. 485. 368.] []
008104 [112.  19. 484. 373.] []
006846 [ 20. 216. 329. 493.] []
003263 [ 12.   5. 324. 479.] []
006122 [135.  13. 485. 304.] []
003498 [ 13.   6. 477. 367.] []
008547 [  0.  35. 444. 322.] []
006386 [ 25.  24. 478. 333.] []
007881 [ 20.   3. 387. 286.] []
006076 [  2.   4. 368. 488.] []
006109 [ 16.  20. 478. 374.] []
003187 [ 18.  16. 486. 321.] []
007904 [ 32.  11. 470. 374.] []
000585 [

008527 [ 20.  89. 448. 374.] []
008129 [ 63.   0. 499. 305.] []
008128 [125.  47. 498. 316.] []
009442 [  3.  24. 394. 294.] []
007851 [ 27.  57. 445. 333.] []
008937 [ 14.   0. 443. 259.] []
008895 [ 96.  14. 489. 346.] []
008714 [ 10.   2. 426. 305.] []
008531 [ 28.  37. 487. 283.] []
008030 [ 75.  80. 409. 319.] []
004752 [  7.  10. 487. 368.] []
007690 [ 27.  99. 495. 374.] []
002338 [ 10.  14. 484. 364.] []
002327 [  8.   6. 321. 487.] []
002326 [  3.   9. 489. 368.] []
002325 [  6.   9. 476. 367.] []
002316 [ 12.  15. 451. 494.] []
002314 [ 11.  22. 317. 492.] []
002313 [ 10.   4. 486. 403.] []
002309 [  0.   0. 498. 318.] []
002303 [ 38.  15. 494. 323.] []
002299 [  0.   4. 492. 374.] []
002289 [  7.   7. 496. 331.] []
002341 [ 26.  34. 299. 248.] []
002283 [ 28.  20. 487. 363.] []
002271 [ 11.   5. 492. 328.] []
002269 [ 13.  21. 327. 491.] []
002245 [  7.  28. 487. 298.] []
002239 [  3.  39. 455. 327.] []
002229 [  9.  12. 492. 327.] []
002217 [  4.   8. 481. 326.] []
002216 [